https://github.com/jadchaar/sec-edgar-api?tab=readme-ov-file

https://gist.github.com/anshoomehra/ead8925ea291e233a5aa2dcaa2dc61b2

In [99]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import requests # requests for the report website
import json
from sec_edgar_api import EdgarClient
from bs4 import BeautifulSoup # Import BeautifulSoup
import re # import re module for REGEXes
import time
import os
import html2text
import codecs

# Split eaech sentences
import nltk
from nltk.tokenize import sent_tokenize
nltk.download('punkt')

import yfinance as yf

# Create a folder for save data
#os.mkdir('Data') 


[nltk_data] Downloading package punkt to /Users/qjy/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


# Request Company tickers and check the cik

In [100]:
CompanyTickers = requests.get('https://www.sec.gov/files/company_tickers.json',
                              headers={'User-Agent':"test@gmail.com"})

CompanyTicker = open('CompanyTickers.json','w+')
CompanyTicker.write(json.dumps(CompanyTickers.json()))
CompanyTicker.close()

CompanyData = pd.DataFrame.from_dict(CompanyTickers.json(), orient='index')
display(CompanyData)

cik_str  ticker                           title
0      320193    AAPL                      Apple Inc.
1      789019    MSFT                  MICROSOFT CORP
2     1045810    NVDA                     NVIDIA CORP
3     1652044   GOOGL                   Alphabet Inc.
4     1018724    AMZN                  AMAZON COM INC
...       ...     ...                             ...
9533  1045450  EPR-PE                  EPR PROPERTIES
9534  1712762   BIAFW  bioAffinity Technologies, Inc.
9535  1456772   OPINL  OFFICE PROPERTIES INCOME TRUST
9536  1848334    OKMN           OKMIN RESOURCES, INC.
9537  1981662   NIVFW             NewGenIvf Group Ltd

[9538 rows x 3 columns]

In [107]:
def FindCompanyCik(Ticker):
    for i in CompanyTickers.json().keys():
        if CompanyTickers.json()[i]['ticker'] ==Ticker:
            print(CompanyTickers.json()[i])
            return CompanyTickers.json()[i]['cik_str']
            break
CompanyName = 'DDD'
Companycik = FindCompanyCik(CompanyName)

{'cik_str': 910638, 'ticker': 'DDD', 'title': '3D SYSTEMS CORP'}


# request the company information and check the 10-Form accn

In [108]:
edgar = EdgarClient(user_agent="test@gmail.com")
test = edgar.get_company_concept(cik=Companycik, taxonomy="us-gaap", tag="AccountsPayableCurrent")

In [109]:
reportRecord = pd.DataFrame.from_dict(test['units']['USD'])
display(reportRecord)

end       val                  accn    fy  fp  form       filed  \
0   2010-12-31  26556000  0000950123-11-069234  2011  Q2  10-Q  2011-07-28   
1   2010-12-31  26556000  0000950123-11-092257  2011  Q3  10-Q  2011-10-27   
2   2010-12-31  26556000  0001193125-12-074109  2011  FY  10-K  2012-02-23   
3   2011-06-30  26669000  0000950123-11-069234  2011  Q2  10-Q  2011-07-28   
4   2011-09-30  25457000  0000950123-11-092257  2011  Q3  10-Q  2011-10-27   
..         ...       ...                   ...   ...  ..   ...         ...   
95  2022-12-31  53826000  0000910638-23-000021  2023  Q2  10-Q  2023-08-09   
96  2022-12-31  53826000  0000910638-23-000025  2023  Q3  10-Q  2023-11-09   
97  2023-03-31  51415000  0000910638-23-000017  2023  Q1  10-Q  2023-05-10   
98  2023-06-30  59023000  0000910638-23-000021  2023  Q2  10-Q  2023-08-09   
99  2023-09-30  46108000  0000910638-23-000025  2023  Q3  10-Q  2023-11-09   

        frame  
0         NaN  
1         NaN  
2   CY2010Q4I  
3   CY2011Q2I  
4   CY2011Q3I  
..        ...  
95        NaN  
96  CY2022Q4I  
97  CY2023Q1I  
98  CY2023Q2I  
99  CY2023Q3I  

[100 rows x 8 columns]

In [110]:
Company10K = reportRecord[reportRecord['form']=='10-K']
display(Company10K)

end       val                  accn    fy  fp  form       filed  \
2   2010-12-31  26556000  0001193125-12-074109  2011  FY  10-K  2012-02-23   
5   2011-12-31  25911000  0001193125-12-074109  2011  FY  10-K  2012-02-23   
9   2011-12-31  25911000  0001193125-13-072822  2012  FY  10-K  2013-02-25   
13  2012-12-31  32095000  0001193125-13-072822  2012  FY  10-K  2013-02-25   
17  2012-12-31  32095000  0001562762-14-000032  2013  FY  10-K  2014-02-28   
21  2013-12-31  51729000  0001562762-14-000032  2013  FY  10-K  2014-02-28   
25  2013-12-31  51729000  0000910638-15-000003  2014  FY  10-K  2015-02-26   
29  2014-12-31  64378000  0000910638-15-000003  2014  FY  10-K  2015-02-26   
33  2014-12-31  64378000  0000910638-16-000016  2015  FY  10-K  2016-03-14   
37  2015-12-31  46869000  0000910638-16-000016  2015  FY  10-K  2016-03-14   
41  2015-12-31  46869000  0000910638-17-000003  2016  FY  10-K  2017-02-28   
45  2016-12-31  40514000  0000910638-17-000003  2016  FY  10-K  2017-02-28   
49  2016-12-31  40514000  0000910638-18-000006  2017  FY  10-K  2018-03-14   
53  2017-12-31  55607000  0000910638-18-000006  2017  FY  10-K  2018-03-14   
57  2017-12-31  55607000  0000910638-19-000004  2018  FY  10-K  2019-02-28   
61  2018-12-31  66722000  0000910638-19-000004  2018  FY  10-K  2019-02-28   
65  2018-12-31  66722000  0000910638-20-000010  2019  FY  10-K  2020-02-26   
69  2019-12-31  49851000  0000910638-20-000010  2019  FY  10-K  2020-02-26   
73  2019-12-31  49851000  0000910638-21-000008  2020  FY  10-K  2021-03-05   
77  2020-12-31  45174000  0000910638-21-000008  2020  FY  10-K  2021-03-05   
81  2020-12-31  45174000  0000910638-22-000013  2021  FY  10-K  2022-03-01   
85  2021-12-31  57366000  0000910638-22-000013  2021  FY  10-K  2022-03-01   
89  2021-12-31  57366000  0000910638-23-000009  2022  FY  10-K  2023-03-16   
93  2022-12-31  53826000  0000910638-23-000009  2022  FY  10-K  2023-03-16   

        frame  
2   CY2010Q4I  
5         NaN  
9   CY2011Q4I  
13        NaN  
17  CY2012Q4I  
21        NaN  
25  CY2013Q4I  
29        NaN  
33  CY2014Q4I  
37        NaN  
41  CY2015Q4I  
45        NaN  
49  CY2016Q4I  
53        NaN  
57  CY2017Q4I  
61        NaN  
65  CY2018Q4I  
69        NaN  
73  CY2019Q4I  
77        NaN  
81  CY2020Q4I  
85        NaN  
89  CY2021Q4I  
93        NaN

In [111]:
Company10K=Company10K.drop_duplicates(['fy'])
Company10K=Company10K.set_index('fy')
display(Company10K)

end       val                  accn  fp  form       filed  \
fy                                                                       
2011  2010-12-31  26556000  0001193125-12-074109  FY  10-K  2012-02-23   
2012  2011-12-31  25911000  0001193125-13-072822  FY  10-K  2013-02-25   
2013  2012-12-31  32095000  0001562762-14-000032  FY  10-K  2014-02-28   
2014  2013-12-31  51729000  0000910638-15-000003  FY  10-K  2015-02-26   
2015  2014-12-31  64378000  0000910638-16-000016  FY  10-K  2016-03-14   
2016  2015-12-31  46869000  0000910638-17-000003  FY  10-K  2017-02-28   
2017  2016-12-31  40514000  0000910638-18-000006  FY  10-K  2018-03-14   
2018  2017-12-31  55607000  0000910638-19-000004  FY  10-K  2019-02-28   
2019  2018-12-31  66722000  0000910638-20-000010  FY  10-K  2020-02-26   
2020  2019-12-31  49851000  0000910638-21-000008  FY  10-K  2021-03-05   
2021  2020-12-31  45174000  0000910638-22-000013  FY  10-K  2022-03-01   
2022  2021-12-31  57366000  0000910638-23-000009  FY  10-K  2023-03-16   

          frame  
fy               
2011  CY2010Q4I  
2012  CY2011Q4I  
2013  CY2012Q4I  
2014  CY2013Q4I  
2015  CY2014Q4I  
2016  CY2015Q4I  
2017  CY2016Q4I  
2018  CY2017Q4I  
2019  CY2018Q4I  
2020  CY2019Q4I  
2021  CY2020Q4I  
2022  CY2021Q4I

# request the 10-K form for company everyyear

In [106]:
for i,row in Company10K.iterrows():  
    accn = row['accn']
    print(accn)
    accnid = accn.replace('-','')
    #print(accnid)
#    time.sleep(1)
    Report_10K = requests.get(f'https://www.sec.gov/Archives/edgar/data/{Companycik}/{accnid}/{accn}.txt',
                              headers={'User-Agent':"test@gmail.com"})
    print(Report_10K)
    raw_10k = Report_10K.text
    # pharse HTML to text file
    Clear10K=html2text.html2text(raw_10k)

    # Save the 10-k report in text
    f = open(f"Data/{CompanyName}-{i}.txt","x+")
    f.write(Clear10K)
    f.close()

0001784031-22-000009
<Response [200]>


AssertionError: unknown status keyword 'N7PIXOM\n' in marked section

# Extract 10K from SEC
https://gist.github.com/anshoomehra/ead8925ea291e233a5aa2dcaa2dc61b2

In [93]:
# AAPL https://www.sec.gov/Archives/edgar/data/320193/000032019323000106/0000320193-23-000106.txt
# Google https://www.sec.gov/Archives/edgar/data/1652044/000165204424000022/0001652044-24-000022.txt

r = requests.get('https://www.sec.gov/Archives/edgar/data/1584754/000161577418008796/0001615774-18-008796.txt',
                headers={'User-Agent':"test@gmail.com"})
raw_10k = r.text
#print(raw_10k)
text=html2text.html2text(raw_10k)
# f = open(f"AAPL2024test.txt","x+")
# f.write(text)
# f.close



In [63]:
print(text)

0001615774-18-008796.txt : 20180829 0001615774-18-008796.hdr.sgml : 20180829
20180829160309 ACCESSION NUMBER: 0001615774-18-008796 CONFORMED SUBMISSION
TYPE: 10-K PUBLIC DOCUMENT COUNT: 92 CONFORMED PERIOD OF REPORT: 20180630
FILED AS OF DATE: 20180829 DATE AS OF CHANGE: 20180829 FILER: COMPANY DATA:
COMPANY CONFORMED NAME: Akoustis Technologies, Inc. CENTRAL INDEX KEY:
0001584754 STANDARD INDUSTRIAL CLASSIFICATION: TELEPHONE & TELEGRAPH APPARATUS
[3661] IRS NUMBER: 331229046 STATE OF INCORPORATION: DE FISCAL YEAR END: 0630
FILING VALUES: FORM TYPE: 10-K SEC ACT: 1934 Act SEC FILE NUMBER: 001-38029
FILM NUMBER: 181044373 BUSINESS ADDRESS: STREET 1: 9805 NORTHCROSS CENTER
COURT, SUITE A CITY: HUNTERSVILLE STATE: NC ZIP: 28078 BUSINESS PHONE:
7026054086 MAIL ADDRESS: STREET 1: 9805 NORTHCROSS CENTER COURT, SUITE A CITY:
HUNTERSVILLE STATE: NC ZIP: 28078 FORMER COMPANY: FORMER CONFORMED NAME:
DANLAX, CORP. DATE OF NAME CHANGE: 20130820  10-K 1 s112155_10k.htm 10-K



**UNITED STATES**

**

Search RegEx to match Item title in Text

In [94]:
def SearchIndexContents(text):
    #IndexContent = re.compile(r'((ITEM \d+\.\ *\s*(.*?)\n))|(Item \d+\.\ *\s*(.*?)\n)').finditer(text)
    IndexContent = re.compile(r'((ITEM\ *\d+\.\ *\s*(.*?)\n))|(Item\ *\d+\.\ *\s*(.*?)\n)', re.IGNORECASE).finditer(text)


    ItemIndex_df = pd.DataFrame([(match.group().strip(), match.start(), match.end()) for match in IndexContent])
    ItemIndex_df.columns = ['Item', 'start', 'end']
    if len(ItemIndex_df) > 16:
        ItemIndex_df = ItemIndex_df[(len(ItemIndex_df)-16):len(ItemIndex_df)]
    ItemIndex_df = ItemIndex_df.reset_index(drop=True)
    display(ItemIndex_df)
    return ItemIndex_df

ReportIndex = SearchIndexContents(text)
#display(ReportIndex)

Item   start     end
0                       ITEM  1.          BUSINESS**   11923   11952
1                    ITEM  2.           PROPERTIES**  125464  125496
2             ITEM  3.           LEGAL PROCEEDINGS**  126754  126793
3       ITEM  4.           MINE SAFETY DISCLOSURES**  127396  127441
4  ITEM 5.           MARKET FOR REGISTRANT'S COMM...  127480  127557
5        ITEM 6.           SELECTED FINANCIAL DATA**  132916  132960
6  ITEM 7.           MANAGEMENT'S DISCUSSION AND ...  133018  133086
7  ITEM 8.            FINANCIAL STATEMENTS AND SU...  168389  168453
8  ITEM 9.            CHANGES IN AND DISAGREEMENT...  287491  287559
9  ITEM  15.         EXHIBITS AND FINANCIAL STATE...  291335  291398

In [65]:
start_index = ReportIndex['start'][4]
print(start_index)

127480


In [97]:
def Extractedtext(dataframe:pd,Item:int,report:str):
    start_items = dataframe[dataframe['Item'].str.contains(f"ITEM\s+{Item}", case=False, regex=True)]
    #print(start_items['start'])
    end_items = dataframe[dataframe['Item'].str.contains(f"ITEM\s+{Item+1}", case=False, regex=True)]
    #print(end_items['start'])
    if (start_items.empty==True) or (end_items.empty==True):
        #print('All in empty')
        return ""
    else:
        start_index = start_items.iloc[0]['start']
        end_index = end_items.iloc[0]['start']
        extracted_text = report[start_index:end_index].strip()
        extracted_text = re.sub(r'\*|\_|\||\#|\-', '', extracted_text)
        extracted_text = re.sub(r'\n', ' ', extracted_text)
        return(extracted_text)

# Extracted_text = Extractedtext(ReportIndex,2,text)
# print(Extracted_text)

In [34]:
item10 = Extractedtext(ReportIndex,1,text)
print(item10)

None


In [98]:
def ExtractESG(text):
    ReportIndex = SearchIndexContents(text)

    item1 = Extractedtext(ReportIndex,1,text)
    item3 = Extractedtext(ReportIndex,3,text)
    item7 = Extractedtext(ReportIndex,7,text)
    item10 = Extractedtext(ReportIndex,10,text)
    item11 = Extractedtext(ReportIndex,11,text)
    item12 = Extractedtext(ReportIndex,12,text)
    All = item1 + ' '+ item3 +' '+ item7 +' '+ item10 +' '+ item11 +' '+ item12
    Split = sent_tokenize(All)
    
    return Split

split = ExtractESG(text)
print(split)

# Create a folder for save data
# os.mkdir('ReportSplitSentences') 
df = pd.DataFrame(split)
# df.columns = ['Sentences']

df.to_csv('/Users/qjy/Desktop/FinTech/Project/Test/ReportSplitSentences/testcsv.csv',index=False)

display(split)

Item   start     end
0                       ITEM  1.          BUSINESS**   11923   11952
1                    ITEM  2.           PROPERTIES**  125464  125496
2             ITEM  3.           LEGAL PROCEEDINGS**  126754  126793
3       ITEM  4.           MINE SAFETY DISCLOSURES**  127396  127441
4  ITEM 5.           MARKET FOR REGISTRANT'S COMM...  127480  127557
5        ITEM 6.           SELECTED FINANCIAL DATA**  132916  132960
6  ITEM 7.           MANAGEMENT'S DISCUSSION AND ...  133018  133086
7  ITEM 8.            FINANCIAL STATEMENTS AND SU...  168389  168453
8  ITEM 9.            CHANGES IN AND DISAGREEMENT...  287491  287559
9  ITEM  15.         EXHIBITS AND FINANCIAL STATE...  291335  291398

All in empty
All in empty
All in empty
['ITEM  1.          BUSINESS    Overview    Akoustis® is a developmentstage company focused on developing, designing, and manufacturing innovative RF filter products for the mobile wireless device industry, including for products such as smartphones and tablets, cellular infrastructure equipment, and WiFi premise equipment.', 'Located between the device\'s antenna and its digital backend, the RF frontend ("RFFE") is the circuitry that performs the analog signal processing and contains components such as amplifiers, filters and switches.', 'To construct the resonators that are the building blocks for the RF filter, we have developed a new and proprietary MEMSbased BAW technology and unique manufacturing flow, called XBAW.', 'Our XBAW process incorporates high purity piezoelectric materials to explore high power, high frequency and wide bandwidth applications.', 'Filters are critical in selecting and rejecting signals, and their performance enables 

['ITEM  1.          BUSINESS    Overview    Akoustis® is a developmentstage company focused on developing, designing, and manufacturing innovative RF filter products for the mobile wireless device industry, including for products such as smartphones and tablets, cellular infrastructure equipment, and WiFi premise equipment.',
 'Located between the device\'s antenna and its digital backend, the RF frontend ("RFFE") is the circuitry that performs the analog signal processing and contains components such as amplifiers, filters and switches.',
 'To construct the resonators that are the building blocks for the RF filter, we have developed a new and proprietary MEMSbased BAW technology and unique manufacturing flow, called XBAW.',
 'Our XBAW process incorporates high purity piezoelectric materials to explore high power, high frequency and wide bandwidth applications.',
 'Filters are critical in selecting and rejecting signals, and their performance enables differentiation in the modules defi

In [68]:
import pandas as pd



matching_items = ReportIndex[ReportIndex['Item'].str.contains(f'Item {1}', case=False)]
print (matching_items.empty)
if matching_items.empty==True:
    print ('no matching')
else:
    print ("matching")

# 示例：查找Item 4
item_number = 6
result = find_item(item_number)
print(result)

True
no matching
                                Item   start     end
5  ITEM 6. SELECTED FINANCIAL DATA**  132916  132960
